In [1]:
# Impoting required packages
import pandas as pd
import numpy as np
import zipfile

# setting default option
pd.set_option("mode.copy_on_write", True)

In [2]:
# View the files present in the Zip file
z = zipfile.ZipFile("../.01_Data/01_Raw/raw_mortality.zip")
z.namelist()

['Underlying Cause of Death, 2009.txt',
 '__MACOSX/',
 '__MACOSX/._Underlying Cause of Death, 2009.txt',
 'Underlying Cause of Death, 2008.txt',
 'Underlying Cause of Death, 2003.txt',
 'Underlying Cause of Death, 2014.txt',
 'Underlying Cause of Death, 2015.txt',
 'Underlying Cause of Death, 2005.txt',
 'Underlying Cause of Death, 2011.txt',
 'Underlying Cause of Death, 2010.txt',
 'Underlying Cause of Death, 2004.txt',
 'Underlying Cause of Death, 2012.txt',
 'Underlying Cause of Death, 2006.txt',
 'Underlying Cause of Death, 2007.txt',
 'Underlying Cause of Death, 2013.txt']

In [3]:
# creating list of files which start with "Underlying" so as to ignore system files
file_list = sorted([f for f in z.namelist() if f.startswith("Underlying")])
file_list

['Underlying Cause of Death, 2003.txt',
 'Underlying Cause of Death, 2004.txt',
 'Underlying Cause of Death, 2005.txt',
 'Underlying Cause of Death, 2006.txt',
 'Underlying Cause of Death, 2007.txt',
 'Underlying Cause of Death, 2008.txt',
 'Underlying Cause of Death, 2009.txt',
 'Underlying Cause of Death, 2010.txt',
 'Underlying Cause of Death, 2011.txt',
 'Underlying Cause of Death, 2012.txt',
 'Underlying Cause of Death, 2013.txt',
 'Underlying Cause of Death, 2014.txt',
 'Underlying Cause of Death, 2015.txt']

In [4]:
# read a single file to understand structure and cleaning rules required
test = pd.read_csv(z.open(file_list[0]), sep="\t")
test.sample(5)

Notes                   County  County Code    Year  Year Code  \
3308   NaN         Union County, TN      47173.0  2003.0     2003.0   
2597   NaN    Rutherford County, NC      37161.0  2003.0     2003.0   
717    NaN      Glascock County, GA      13125.0  2003.0     2003.0   
2261   NaN  Hillsborough County, NH      33011.0  2003.0     2003.0   
3181   NaN     McPherson County, SD      46089.0  2003.0     2003.0   

                             Drug/Alcohol Induced Cause  \
3308          All other non-drug and non-alcohol causes   
2597          All other non-drug and non-alcohol causes   
717           All other non-drug and non-alcohol causes   
2261  Drug poisonings (overdose) Unintentional (X40-...   
3181          All other non-drug and non-alcohol causes   

     Drug/Alcohol Induced Cause Code  Deaths  
3308                              O9   165.0  
2597                              O9   731.0  
717                               O9    40.0  
2261                              D1    23.0  
3181                              O9    39.0

In [5]:
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4102 entries, 0 to 4101
Data columns (total 8 columns):
 #   Column                           Non-Null Count  Dtype  
---  ------                           --------------  -----  
 0   Notes                            15 non-null     object 
 1   County                           4087 non-null   object 
 2   County Code                      4087 non-null   float64
 3   Year                             4087 non-null   float64
 4   Year Code                        4087 non-null   float64
 5   Drug/Alcohol Induced Cause       4087 non-null   object 
 6   Drug/Alcohol Induced Cause Code  4087 non-null   object 
 7   Deaths                           4087 non-null   float64
dtypes: float64(4), object(4)
memory usage: 256.5+ KB


In [6]:
# viewing the rows which have non-null values in Notes column
test[test["Notes"].notnull()]

Notes County  County Code  \
4087                                                ---    NaN          NaN   
4088      Dataset: Underlying Cause of Death, 1999-2017    NaN          NaN   
4089                                  Query Parameters:    NaN          NaN   
4090  Group By: County; Year; Drug/Alcohol Induced C...    NaN          NaN   
4091                              Show Totals: Disabled    NaN          NaN   
4092                         Show Zero Values: Disabled    NaN          NaN   
4093                             Show Suppressed: False    NaN          NaN   
4094                                                ---    NaN          NaN   
4095  Help: See http://wonder.cdc.gov/wonder/help/uc...    NaN          NaN   
4096                                                ---    NaN          NaN   
4097  Suggested Citation: Centers for Disease Contro...    NaN          NaN   
4098  1999-2017 on CDC WONDER Online Database, relea...    NaN          NaN   
4099  compiled from data provided by the 57 vital st...    NaN          NaN   
4100  at http://wonder.cdc.gov/ucd-icd10.html on Oct...    NaN          NaN   
4101                                                ---    NaN          NaN   

      Year  Year Code Drug/Alcohol Induced Cause  \
4087   NaN        NaN                        NaN   
4088   NaN        NaN                        NaN   
4089   NaN        NaN                        NaN   
4090   NaN        NaN                        NaN   
4091   NaN        NaN                        NaN   
4092   NaN        NaN                        NaN   
4093   NaN        NaN                        NaN   
4094   NaN        NaN                        NaN   
4095   NaN        NaN                        NaN   
4096   NaN        NaN                        NaN   
4097   NaN        NaN                        NaN   
4098   NaN        NaN                        NaN   
4099   NaN        NaN                        NaN   
4100   NaN        NaN                        NaN   
4101   NaN        NaN                        NaN   

     Drug/Alcohol Induced Cause Code  Deaths  
4087                             NaN     NaN  
4088                             NaN     NaN  
4089                             NaN     NaN  
4090                             NaN     NaN  
4091                             NaN     NaN  
4092                             NaN     NaN  
4093                             NaN     NaN  
4094                             NaN     NaN  
4095                             NaN     NaN  
4096                             NaN     NaN  
4097                             NaN     NaN  
4098                             NaN     NaN  
4099                             NaN     NaN  
4100                             NaN     NaN  
4101                             NaN     NaN

We can clean notes in a similar was as we did for the other dataset

In [7]:
# read data from all the files and append to list
df_list = []
for file in file_list:
    # read individual files
    df_temp = pd.read_csv(z.open(file), sep="\t")

    # drop the notes columns and remove rows with null values in State column
    df_temp.drop(columns=["Notes"], inplace=True)
    df_temp.dropna(subset=["County"], inplace=True)

    # add the cleaned temp Df to the main list
    df_list.append(df_temp)

In [8]:
# create the dataframe
df = pd.concat(df_list, ignore_index=True)
df.sample(5)

County  County Code    Year  Year Code  \
32856    Sequoyah County, OK      40135.0  2010.0     2010.0   
11096       Stark County, OH      39151.0  2005.0     2005.0   
48071       Butte County, CA       6007.0  2014.0     2014.0   
2822     Garfield County, OK      40047.0  2003.0     2003.0   
35841  Terrebonne Parish, LA      22109.0  2011.0     2011.0   

                              Drug/Alcohol Induced Cause  \
32856  Drug poisonings (overdose) Unintentional (X40-...   
11096  Drug poisonings (overdose) Unintentional (X40-...   
48071                   All other alcohol-induced causes   
2822           All other non-drug and non-alcohol causes   
35841          All other non-drug and non-alcohol causes   

      Drug/Alcohol Induced Cause Code Deaths  
32856                              D1   11.0  
11096                              D1   16.0  
48071                              A9   42.0  
2822                               O9  676.0  
35841                              O9  952.0

In [9]:
# check for null values
df.isnull().sum()

County                             0
County Code                        0
Year                               0
Year Code                          0
Drug/Alcohol Induced Cause         0
Drug/Alcohol Induced Cause Code    0
Deaths                             0
dtype: int64

In [10]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 57241 entries, 0 to 57240
Data columns (total 7 columns):
 #   Column                           Non-Null Count  Dtype  
---  ------                           --------------  -----  
 0   County                           57241 non-null  object 
 1   County Code                      57241 non-null  float64
 2   Year                             57241 non-null  float64
 3   Year Code                        57241 non-null  float64
 4   Drug/Alcohol Induced Cause       57241 non-null  object 
 5   Drug/Alcohol Induced Cause Code  57241 non-null  object 
 6   Deaths                           57241 non-null  object 
dtypes: float64(3), object(4)
memory usage: 3.1+ MB


In [11]:
# Cleaning the data
df2 = df.copy()

# Pad county code with 0 for consistency with other data sets
df2["County Code"] = df2["County Code"].astype(int).astype(str).str.zfill(5)

# Convert Year to Int
df2["Year"] = df2["Year"].astype(int)

# Convert Deaths to Int
df2["Deaths"] = df2["Deaths"].replace("Missing", np.nan)
df2["Deaths"] = (
    df2["Deaths"].astype(float).astype("Int64")
)  # making it as int64 so that we retain null values

In [12]:
# Check the causes of death present
df2["Drug/Alcohol Induced Cause"].unique()

array(['All other non-drug and non-alcohol causes',
       'Drug poisonings (overdose) Unintentional (X40-X44)',
       'All other alcohol-induced causes',
       'All other drug-induced causes',
       'Drug poisonings (overdose) Suicide (X60-X64)',
       'Drug poisonings (overdose) Undetermined (Y10-Y14)',
       'Alcohol poisonings (overdose) (X45, X65, Y15)',
       'Drug poisonings (overdose) Homicide (X85)'], dtype=object)

In [13]:
# Filter the data to only include drug related deaths
required_causes = [
    "Drug poisonings (overdose) Unintentional (X40-X44)",
    "All other drug-induced causes",
    "Drug poisonings (overdose) Homicide (X85)",
    "Drug poisonings (overdose) Suicide (X60-X64)",
    "Drug poisonings (overdose) Undetermined (Y10-Y14)",
]

In [14]:
df3 = df2[df2["Drug/Alcohol Induced Cause"].isin(required_causes)]

In [15]:
# remove extra columns
df3.drop(columns=["Year Code", "Drug/Alcohol Induced Cause Code"], inplace=True)

In [16]:
df3.sample(5)

County County Code  Year  \
30939     Wabash County, IN       18169  2010   
36770     Cayuga County, NY       36011  2011   
2317     Passaic County, NJ       34031  2003   
9869   Frederick County, MD       24021  2005   
22426       Boyd County, KY       21019  2008   

                              Drug/Alcohol Induced Cause  Deaths  
30939  Drug poisonings (overdose) Unintentional (X40-...      10  
36770  Drug poisonings (overdose) Unintentional (X40-...      10  
2317   Drug poisonings (overdose) Unintentional (X40-...      28  
9869   Drug poisonings (overdose) Undetermined (Y10-Y14)      13  
22426  Drug poisonings (overdose) Unintentional (X40-...      24

In [17]:
# renaming columns
df3.rename(
    columns={"Drug/Alcohol Induced Cause": "Cause", "County Code": "County_Code"},
    inplace=True,
)

In [18]:
# use fips file to generate proper county name and state
fips = pd.read_csv("../.01_Data/01_Raw/county_fips.csv")
fips["countyfips"] = fips["countyfips"].astype(str).str.zfill(5)

In [19]:
# merge with fips
# performing left join to get the county names
df4 = pd.merge(
    df3,
    fips,
    how="left",
    left_on="County_Code",
    right_on="countyfips",
    validate="m:1",
    indicator=True,
)
df4.sample(5)

County County_Code  Year  \
1799      Hidalgo County, TX       48215  2005   
9215   Greenville County, SC       45045  2014   
2843    St. Clair County, IL       17163  2007   
1063  Northampton County, PA       42095  2004   
4368       Newton County, GA       13217  2009   

                                                  Cause  Deaths BUYER_COUNTY  \
1799                      All other drug-induced causes      10      HIDALGO   
9215       Drug poisonings (overdose) Suicide (X60-X64)      10   GREENVILLE   
2843  Drug poisonings (overdose) Unintentional (X40-...      15  SAINT CLAIR   
1063  Drug poisonings (overdose) Unintentional (X40-...      16  NORTHAMPTON   
4368  Drug poisonings (overdose) Unintentional (X40-...      13       NEWTON   

     BUYER_STATE countyfips _merge  
1799          TX      48215   both  
9215          SC      45045   both  
2843          IL      17163   both  
1063          PA      42095   both  
4368          GA      13217   both

In [20]:
# Validate if merge went well
df4["_merge"].value_counts()

_merge
both          10432
left_only         0
right_only        0
Name: count, dtype: int64

In [21]:
# select required colums
df5 = df4[["BUYER_STATE", "BUYER_COUNTY", "County_Code", "Year", "Cause", "Deaths"]]

# rename columns
df5 = df5.rename(columns={"BUYER_COUNTY": "County", "BUYER_STATE": "State_Code"})

In [22]:
df5.sample(5)

State_Code    County County_Code  Year  \
2201         MI   BERRIEN       26021  2006   
3238         TN   BRADLEY       47011  2007   
8909         MS   MADISON       28089  2014   
7578         AZ  MARICOPA       04013  2013   
5624         SC    OCONEE       45073  2010   

                                                  Cause  Deaths  
2201  Drug poisonings (overdose) Unintentional (X40-...      21  
3238  Drug poisonings (overdose) Unintentional (X40-...      23  
8909  Drug poisonings (overdose) Unintentional (X40-...      12  
7578  Drug poisonings (overdose) Undetermined (Y10-Y14)      89  
5624  Drug poisonings (overdose) Unintentional (X40-...      16

In [23]:
# Add state names to maitain consistency with population data
abbreviations = pd.read_csv("../.01_Data/01_Raw/state_abbreviations.csv")
abbreviations.sample(5)

state abbrev code
13        Illinois   Ill.   IL
40  South Carolina   S.C.   SC
10         Georgia    Ga.   GA
34    North Dakota   N.D.   ND
38    Pennsylvania    Pa.   PA

In [24]:
# rename colums to match with the main dataframe
abbreviations = abbreviations.rename(
    columns={
        "state": "State",
        "code": "State_Code",
    }
)

In [25]:
# Merge
df6 = pd.merge(
    df5,
    abbreviations[["State", "State_Code"]],
    how="left",
    on="State_Code",
    validate="m:1",
    indicator=True,
)
df6.sample(5)

State_Code     County County_Code  Year  \
6372         OH   DELAWARE       39041  2011   
5339         MI  WASHTENAW       26161  2010   
8433         WV      WAYNE       54099  2013   
4737         OR  CLACKAMAS       41005  2009   
93           CO    LARIMER       08069  2003   

                                                  Cause  Deaths  \
6372  Drug poisonings (overdose) Unintentional (X40-...      11   
5339  Drug poisonings (overdose) Undetermined (Y10-Y14)      19   
8433  Drug poisonings (overdose) Unintentional (X40-...      17   
4737  Drug poisonings (overdose) Unintentional (X40-...      32   
93    Drug poisonings (overdose) Unintentional (X40-...      13   

              State _merge  
6372           Ohio   both  
5339       Michigan   both  
8433  West Virginia   both  
4737         Oregon   both  
93         Colorado   both

In [26]:
# Validate if merge went well
df6["_merge"].value_counts()

_merge
both          10432
left_only         0
right_only        0
Name: count, dtype: int64

In script file we dont need the merge indicator column, so it will not be used there

In [27]:
# reorder columns to match population data
df6 = df6[["State", "State_Code", "County", "County_Code", "Year", "Cause", "Deaths"]]
df6.sample(5)

State State_Code          County County_Code  Year  \
2398             Ohio         OH        TRUMBULL       39155  2006   
5703             Utah         UT           DAVIS       49011  2010   
10208  South Carolina         SC           AIKEN       45003  2015   
242          Maryland         MD  PRINCE GEORGES       24033  2003   
1250       California         CA           MARIN       06041  2005   

                                                   Cause  Deaths  
2398   Drug poisonings (overdose) Unintentional (X40-...      30  
5703   Drug poisonings (overdose) Unintentional (X40-...      22  
10208  Drug poisonings (overdose) Unintentional (X40-...      30  
242    Drug poisonings (overdose) Unintentional (X40-...      14  
1250   Drug poisonings (overdose) Undetermined (Y10-Y14)      16